In [1]:
!pip install tensorflow-gpu==1.15.0

     |████████████████████████████████| 411.5MB 36kB/s 
     |████████████████████████████████| 3.8MB 58.7MB/s 
     |████████████████████████████████| 51kB 7.2MB/s 
     |████████████████████████████████| 512kB 51.8MB/s 
  Created wheel for gast: filename=gast-0.2.2-cp36-none-any.whl size=7542 sha256=bfc0fefda8ea12cabbb36566e787aa5678cf6ace8581bc4107d8085a59648216
  Stored in directory: /root/.cache/pip/wheels/5c/2e/7e/a1d4d4fcebe6c381f378ce7743a3ced3699feb89bcfbdadadd
Successfully built gast
ERROR: tensorflow 2.3.0 has requirement gast==0.3.3, but you'll have gast 0.2.2 which is incompatible.
ERROR: tensorflow 2.3.0 has requirement tensorboard<3,>=2.3.0, but you'll have tensorboard 1.15.0 which is incompatible.
ERROR: tensorflow 2.3.0 has requirement tensorflow-estimator<2.4.0,>=2.3.0, but you'll have tensorflow-estimator 1.15.1 which is incompatible.
ERROR: tensorflow-probability 0.11.0 has requirement gast>=0.3.2, but you'll have gast 0.2.2 which is incompatible.
  Found existing i

In [2]:
# See if running on GPU
import tensorflow as tf
device_name = tf.test.gpu_device_name()
if device_name != '/device:GPU:0':
  raise SystemError('GPU device not found')
print('Found GPU at: {}'.format(device_name))

Found GPU at: /device:GPU:0


In [3]:
!pip install keras==2.2.4
!pip install matplotlib
!pip install pillow==7.1.2

     |████████████████████████████████| 317kB 7.4MB/s 
  Found existing installation: Keras 2.4.3
    Uninstalling Keras-2.4.3:
      Successfully uninstalled Keras-2.4.3
     |████████████████████████████████| 2.1MB 5.6MB/s 
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
  Found existing installation: Pillow 7.0.0
    Uninstalling Pillow-7.0.0:
      Successfully uninstalled Pillow-7.0.0


In [1]:
import os
import matplotlib.pyplot as plt
import numpy as np

from keras.datasets import cifar10, mnist
from keras.initializers import RandomNormal
from keras.layers import (BatchNormalization, Conv2D, Conv2DTranspose, 
              Dense, Dropout, Flatten, Input, Reshape, 
              UpSampling2D, ZeroPadding2D)
from keras.layers.advanced_activations import LeakyReLU
from keras.models import Model, Sequential
from keras.optimizers import Adam

%matplotlib inline

Using TensorFlow backend.


In [3]:
# Consistent results
np.random.seed(10)

# The dimesnion of z
noise_dim = 100

batch_size = 16
steps_per_epoch = 312
epochs = 800

save_path = "/content/drive/My Drive/CycleGan Monet/GANS Tutorial/dcgan-images"

im_rows, im_cols, channels = 32, 32, 3

optimizer = Adam(0.0002, 0.5)

In [ ]:
# Create path for saving images
if save_path != None and not os.path.isdir(save_path):
  os.mkdir(save_path)

In [ ]:

# Load and pre-process data
(x_train, y_train), (x_test, y_test) = cifar10.load_data()
# Normalize to between -1 and 1
x_train = (x_train.astype(np.float32) - 127.5) / 127.5

# Reshape and only save cat images
# x_train.shape = (5000, 32, 32, 3)
x_train = x_train[np.where(y_train == 0)[0]].reshape(-1, im_rows, im_cols, channels)

#x_train.shape == (50000, 32, 32, 3)

In [ ]:
def create_generator():
    generator = Sequential()
    
    # Starting size
    d = 4
    generator.add(Dense(d*d*256, kernel_initializer=RandomNormal(0, 0.02), input_dim=noise_dim))
    generator.add(LeakyReLU(0.2))
    # 4x4x256
    generator.add(Reshape((d, d, 256)))
    
    # 8x8x128
    generator.add(Conv2DTranspose(128, (4, 4), strides=2, padding='same', kernel_initializer=RandomNormal(0, 0.02)))
    generator.add(LeakyReLU(0.2))
    
    # 16x16*128
    generator.add(Conv2DTranspose(128, (4, 4), strides=2, padding='same', kernel_initializer=RandomNormal(0, 0.02)))
    generator.add(LeakyReLU(0.2))
    
    # 32x32x128
    generator.add(Conv2DTranspose(128, (4, 4), strides=2, padding='same', kernel_initializer=RandomNormal(0, 0.02)))
    generator.add(LeakyReLU(0.2))
    
    # 32x32x3
    generator.add(Conv2D(channels, (3, 3), padding='same', activation='tanh', kernel_initializer=RandomNormal(0, 0.02)))
    
    generator.compile(loss='binary_crossentropy', optimizer=optimizer)
    return generator

In [ ]:

def create_discriminator():
    discriminator = Sequential()
    
    discriminator.add(Conv2D(64, (3, 3), padding='same', kernel_initializer=RandomNormal(0, 0.02), input_shape=(im_cols, im_rows, channels)))
    discriminator.add(LeakyReLU(0.2))
    
    discriminator.add(Conv2D(128, (3, 3), strides=2, padding='same', kernel_initializer=RandomNormal(0, 0.02)))
    discriminator.add(LeakyReLU(0.2))
    
    discriminator.add(Conv2D(128, (3, 3), strides=2, padding='same', kernel_initializer=RandomNormal(0, 0.02)))
    discriminator.add(LeakyReLU(0.2))
    
    discriminator.add(Conv2D(256, (3, 3), strides=2, padding='same', kernel_initializer=RandomNormal(0, 0.02)))
    discriminator.add(LeakyReLU(0.2))
    
    discriminator.add(Flatten())
    discriminator.add(Dropout(0.4))
    discriminator.add(Dense(1, activation='sigmoid'))
    
    discriminator.compile(loss='binary_crossentropy', optimizer=optimizer)
    return discriminator

In [ ]:
# Create the generator and discriminator
discriminator = create_discriminator()
generator = create_generator()

In [ ]:
# Make the discriminator untrainable when we are training the 
# generator. This does not effect the discriminator by itself
discriminator.trainable=False

# Link the two models to create the GAN
gan_input = Input(shape=(noise_dim,))
fake_image = generator(gan_input)

gan_output = discriminator(fake_image)

gan = Model(gan_input, gan_output)
gan.compile(loss="binary_crossentropy", optimizer=optimizer)

In [ ]:
# Display images and save them if the epoch number is specified
def show_image(noise, epoch=None):
  generated_images = generator.predict(noise)
  plt.figure(figsize=(10, 10))

  for i, image in enumerate(generated_images):
    plt.subplot(10, 10, i+1)
    if channels == 1:
      plt.imshow(image.reshape((im_rows, im_cols)), cmap="gray")
    else:
      plt.imshow(image.reshape((im_rows, im_cols, channels)))
    plt.axis("off")

  plt.tight_layout()

  if epoch != None and save_path != None:
    plt.savefig("{}/gan-images_epoch-{}.png".format(save_path, epoch))

In [ ]:
# Constant Noise for viewing how the GAN process (Generate pseudo 
# image from these noise)
static_noise = np.random.normal(0, 1, size=(100, noise_dim))

# train the GAN
for epoch in range(epochs):
  for batch in range(steps_per_epoch):
    noise = np.random.normal(0, 1, size=(batch_size, noise_dim))
    fake_x = generator.predict(noise)

    real_x = x_train[np.random.randint(0, x_train.shape[0], size=batch_size)]

    # Concatenate the data with label 1s and 0s
    x = np.concatenate((real_x, fake_x))

    disc_y = np.zeros(2*batch_size)
    # label smoothing
    disc_y[:batch_size] = 0.9

    d_loss = discriminator.train_on_batch(x, disc_y)

    y_gen = np.ones(batch_size)
    g_loss = gan.train_on_batch(noise, y_gen)

  print("Epoch: {} \t Discriminator Loss: {} \t\t Generator Loss: {}".format(epoch, d_loss, g_loss))
  if epoch % 2 == 0:
    show_image(static_noise, epoch)

/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow w

Epoch: 0 	 Discriminator Loss: 0.5769515037536621 		 Generator Loss: 1.753035545349121


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

Epoch: 1 	 Discriminator Loss: 0.7371872663497925 		 Generator Loss: 1.2403340339660645


...

Epoch: 743 	 Discriminator Loss: 0.22590693831443787 		 Generator Loss: 4.48023796081543


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

Epoch: 744 	 Discriminator Loss: 0.1928696185350418 		 Generator Loss: 4.312016010284424


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

Epoch: 745 	 Discriminator Loss: 0.19163867831230164 		 Generator Loss: 4.579262733459473


In [4]:
# Turn the training process into GIF
from PIL import Image, ImageDraw

frames = []
for image in os.listdir(save_path):
  frames.append(Image.open(save_path + "/" + image))
frames[0].save("/content/drive/My Drive/CycleGan Monet/GANS Tutorial/dcgan_taining.gif", format="GIF", append_images=frames[1:], save_all=True, duration=50, loop=0)

In [ ]:
# Save the model
discriminator.save("/content/drive/My Drive/CycleGan Monet/GANS Tutorial/fcdiscriminator.hdf5")
generator.save("/content/drive/My Drive/CycleGan Monet/GANS Tutorial/fcgenerator.hdf5")
gan.save("/content/drive/My Drive/CycleGan Monet/GANS Tutorial/fcgan.hdf5")

##Notes  
* numpy.where:  https://www.geeksforgeeks.org/numpy-where-in-python/

In [5]:
cd "/content/drive/My Drive/CycleGan Monet"

/content/drive/My Drive/CycleGan Monet


In [ ]:
!git add .

In [ ]:
!git comitt -m ""

In [ ]:
print(x_train.shape)

(5000, 32, 32, 3)
